In [3]:
# %load_ext autoreload
# %autoreload 2
%load_ext tuna

import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)

import matplotlib.pyplot as plt
import numpy as np
import dill
import os
import seaborn as sns
import torch
import pandas as pd

from collections import namedtuple
from hmmlearn.hmm import MultinomialHMM
from scipy.special import logsumexp
from scipy.stats import multivariate_normal
from spn.algorithms.Inference import log_likelihood

# from rspnlib.models import RSPN, EMTrainingParams
# from rspnlib.models.hmm import HmmRSPN
# from rspnlib.models.iohmm import (
#     IoHmmRSPN,
#     ExtendedIoHmmRSPN,
#     ContinuousIoHmmRSPN,
#     OverparametrisedIoHmmRSPN,
#     OverparametrisedContinuousIoHmmRSPN,
#     ExtendedOverparametrisedContinuousIoHmmRSPN,
# )
# from rspnlib.evaluation import (
#     compute_metrics,
#     get_empty_metrics,
#     add_metrics,
#     print_aggregate_metrics,
#     evaluate_rspn_one_step_ahead_prediction,
#     evaluate_rspn_observation_regression,
# )
# from experiment_utils.datasets.vasopressors_dataset import load_vasopressors_dataset
from experiment_utils.datasets.mimic_continuous_dataset import load_mimic_dataset
# from experiment_utils.baselines.lstm import train_eval_lstm
# from experiment_utils.baselines.most_common_class import train_eval_most_common_baseline


from engine_dataset import generate_engine_dataset, generate_engine_datasets

from oSLRAU_run import get_data
from spn.structure.leaves.parametric.Parametric import Gaussian, Bernoulli, Categorical,  In_Latent, Multivariate_Gaussian
from spn.structure.Base import Context
from spn.algorithms.LearningWrappers import learn_parametric
from spn.io.Graphics import plot_spn
import numpy as np
from spn.algorithms.Inference import log_likelihood
from sklearn.model_selection import train_test_split
from spn.algorithms.oSLRAU import oSLRAU, oSLRAUParams
from spn.algorithms.RSPN import RSPN
from spn.algorithms.TransformStructure import Prune ,Prune_oSLRAU

from hmmlearn import hmm
from spn.algorithms.Inference import log_likelihood

The tuna extension is already loaded. To reload it, use:
  %reload_ext tuna


# MIMIC Experiments

In [4]:
SEQ_LENGTH = 8
NUM_STATES = 20
NUM_SEEDS = 5
SEEDS = range(42, 42 + NUM_SEEDS)

train_mimic_datasets, test_mimic_datasets = load_mimic_dataset(
    seq_length=SEQ_LENGTH,
)
num_inputs = (
    int(
        np.max(train_mimic_datasets[0].inputs_raw)
    )
    + 1
)
observations_dim = 3

  0%|          | 0/6052 [00:00<?, ?it/s]

Loaded 5967 data points
Partitioning into folds...
Done!


In [5]:
import pickle
train_mimic_datasets, test_mimic_datasets = pickle.load(open('./data_splits/data.pkl', 'rb'))
observations_dim = 3
num_inputs = 2

<h2> oSLRAU  </h2>

In [13]:
def train_rspn_mimic(train_data, test_data, epoch, rspn=None, os_args=None):

    if len(train_data.shape) == 3: train_data = np.squeeze(train_data)
    if len(test_data.shape) == 3: test_data = np.squeeze(test_data)

    if rspn is None:
    
        rspn = RSPN(num_variables=os_args["num_variables"], num_latent_variables=os_args["num_latent_variables"], num_latent_values=os_args["num_latent_values"])
        first_mini_batch = train_data[0:os_args["mini_batch_size"]]
        n = first_mini_batch.shape[1]

        print(f"n: {n}") # = num_time_steps_mix * n_dim
        
        context = [Gaussian, Gaussian, Gaussian, Bernoulli]*(int(n/4)) # Bernoulli Categorical
        ds_context = Context(parametric_types=context).add_domains(first_mini_batch[:, :os_args["num_variables"]])
        spn, initial_template_spn, top_spn = rspn.build_initial_template(first_mini_batch, ds_context, os_args["len_sequence_varies"])

    
    no_of_minibatches = int(train_data.shape[0] / os_args["mini_batch_size"])

    print(f"no of minibatches: {no_of_minibatches}")

    
    for i in range(1, no_of_minibatches):
        mini_batch = train_data[i * os_args["mini_batch_size"]: (i+1) * os_args["mini_batch_size"]]
    
        update_template = False
        
        # if (i % os_args["update_after_no_min_batches"] == 0) and (i!=0) :
        #if i % os_args["update_after_no_min_batches"] == 0 and i<=60 and epoch == 0:
        if i == 10 and epoch == 0:
            print(i)
            update_template = True

        try:
            template_spn = rspn.learn_rspn(mini_batch, update_template, os_args["os_params"], os_args["unroll"],
                                            os_args["full_update"], os_args["update_leaves"],
                                            os_args["len_sequence_varies"])
        
        except Exception:
            print(f"==>> mini_batch: {mini_batch}")
            assert 0 == 1
           
            
    test_ll = np.sum(rspn.log_likelihood(test_data, os_args["unroll"], os_args["len_sequence_varies"]))


    return test_ll, rspn, template_spn

In [14]:
def final_ll_mimic(data, num_epochs=1, do_plot_spn=True, os_args=None, split_data=False):
    ll = -np.inf
    rspn=None
    if split_data:
        train_data, val_data= train_test_split(data, test_size=0.1, random_state=42)
    
    else:
        train_data, val_data = data, data
    for epoch in range(num_epochs):
        print(train_data.shape)
        
        
        epoch_ll, rspn, template_spn = train_rspn_mimic(train_data, val_data, epoch, rspn, os_args)        
        print(f"epoch_ll: {epoch_ll}")
        
        ll = epoch_ll
        del template_spn

    print(f" \n\n\n final ll: {ll}\n\n\n")

    if do_plot_spn:
        plot_spn(template_spn, 'rspn_final_template.pdf')
    
    return rspn

In [15]:
np.unique(train_mimic_datasets[0].inputs_raw)

#train_mimic_datasets[0].observations_raw_continuous.shape

array([0, 1], dtype=int32)

In [16]:
def process_ds(ds):
    raw_inputs = ds.inputs_raw
    obs_raw_cont = ds.observations_raw_continuous

    comb_ds = []
    for i in range(raw_inputs.shape[0]):
        comb_ds_i = []
        for j in range(raw_inputs.shape[1]):
             comb_ds_j = [*list(obs_raw_cont[i, j*3: (j+1)*3]), raw_inputs[i,j]]
             comb_ds_i.append(comb_ds_j)

        comb_ds.append(comb_ds_i)

    comb_ds = np.array(comb_ds)
    comb_ds = comb_ds.reshape(raw_inputs.shape[0], -1)

    return comb_ds


In [17]:
n_states = 2
n_dim = 4

num_time_steps = 8

oSLRAU_params = oSLRAUParams(mergebatch_threshold=128, corrthresh=0.1, mvmaxscope=1, equalweight=True, currVals=True)

os_args = {
    "num_variables": num_time_steps * n_dim,
    "num_latent_variables" : 2,
    "num_latent_values" : 2,
    "unroll" : "backward",
    "full_update" : False,
    "update_leaves" : True,
    "len_sequence_varies" : False,
    "mini_batch_size" : 5,
    "update_after_no_min_batches" : 20,
    "os_params": oSLRAU_params
    }

In [30]:
log_likelihoods = []
rspn_mimic_models = []
train_ds_list = []
test_ds_list = []

In [31]:
base_seed = SEEDS[0]
seed_dict = {SEEDS[i]: i for i in range(len(SEEDS))}
seed_ls = SEEDS # [SEEDS[1]]
#del rspn_mimic

for seed in seed_ls:
    i = seed_dict[seed]
    print(f"——————————[ Running experiment for seed {seed} ]——————————")
    train_ds, test_ds = process_ds(train_mimic_datasets[i]), process_ds(test_mimic_datasets[i])
    train_ds_list.append(train_ds)
    test_ds_list.append(test_ds)
    rspn_mimic = final_ll_mimic(train_ds, num_epochs=3, do_plot_spn=False, os_args=os_args)
    rspn_test_ll_mimic = np.sum(rspn_mimic.log_likelihood(test_ds, os_args["unroll"], os_args["len_sequence_varies"]))
    print(f"seed {seed}: log likelihood: {rspn_test_ll_mimic}")
    log_likelihoods.append(rspn_test_ll_mimic)
    rspn_mimic_models.append(rspn_mimic)

——————————[ Running experiment for seed 42 ]——————————
(4773, 32)
n: 32
==>> data.shape: (5, 32)
len(self.meta_types): 32
self.meta_types.values(): dict_values([<MetaType.REAL: 1>, <MetaType.REAL: 1>, <MetaType.REAL: 1>, <MetaType.BINARY: 2>, <MetaType.REAL: 1>, <MetaType.REAL: 1>, <MetaType.REAL: 1>, <MetaType.BINARY: 2>, <MetaType.REAL: 1>, <MetaType.REAL: 1>, <MetaType.REAL: 1>, <MetaType.BINARY: 2>, <MetaType.REAL: 1>, <MetaType.REAL: 1>, <MetaType.REAL: 1>, <MetaType.BINARY: 2>, <MetaType.REAL: 1>, <MetaType.REAL: 1>, <MetaType.REAL: 1>, <MetaType.BINARY: 2>, <MetaType.REAL: 1>, <MetaType.REAL: 1>, <MetaType.REAL: 1>, <MetaType.BINARY: 2>, <MetaType.REAL: 1>, <MetaType.REAL: 1>, <MetaType.REAL: 1>, <MetaType.BINARY: 2>, <MetaType.REAL: 1>, <MetaType.REAL: 1>, <MetaType.REAL: 1>, <MetaType.BINARY: 2>])
len(self.meta_types.values()): 32
data[:, col]: [115.   65.   82.   86.5 110. ]
==>> domain_values: [65.0, 115.0]
feature_meta_type: MetaType.REAL
==>> domain_values: [65.0, 115.0]
l

/Users/dariyankhan/Library/CloudStorage/OneDrive-ImperialCollegeLondon/Work (one drive)/Imperial/MIT/exchange_year/summer-UROP-knowledge-distillation/policy_stuff/policy-learn/SPFlow/src/spn/algorithms/oSLRAU.py:76: RuntimeWarning: divide by zero encountered in log
  w_children_log_probs[:, i] = lls_per_node[parent_result, c.id] + np.log(node.weights[i])


==>> result: [[ -87.92737787]
 [-104.43818019]
 [-101.1807508 ]
 [ -86.00035866]
 [ -86.52636824]]
==>> result: [[ -87.92737787]
 [-104.43818019]
 [-101.1807508 ]
 [ -88.0501612 ]
 [ -86.52636824]]
==>> in_latent_dict: {In_LatentNode_1: array([0, 1, 2, 3, 4])}
==>> result: [[-83.40413559]
 [-91.56535508]
 [-91.97294389]
 [-87.92830729]
 [-85.92921769]]
==>> result: [[-83.40413559]
 [-91.56535508]
 [-91.97294389]
 [-87.92830729]
 [-86.66518743]]
==>> in_latent_dict: {In_LatentNode_1: array([0, 1, 2, 3, 4])}
==>> result: [[-106.79058717]
 [ -89.02986785]
 [ -86.85107009]
 [ -90.29673452]
 [ -96.09542682]]
==>> result: [[-106.79058717]
 [ -89.02986785]
 [ -86.85107009]
 [ -92.1113547 ]
 [ -96.09542682]]
==>> in_latent_dict: {In_LatentNode_1: array([0, 1, 2, 3, 4])}
==>> result: [[-89.81244136]
 [-93.64743084]
 [-89.31997109]
 [-86.29815016]
 [-95.48559361]]
==>> result: [[-89.81244136]
 [-93.64743084]
 [-90.68182292]
 [-86.29815016]
 [-95.48559361]]
==>> in_latent_dict: {In_LatentNode_1: 

In [20]:
log_likelihoods

[-112412.50376934174,
 -108213.71369434081,
 -108035.95166376798,
 -113649.07080729176]

In [21]:
# print(np.mean(log_likelihoods))
#log_likelihoods
print(f"Mean: {np.array(log_likelihoods).mean()}")
print(f"STD: {np.array(log_likelihoods).std()}")

Mean: -110577.80998368558
STD: 2492.4254912419897


In [22]:
rspn_mimic_models

In [26]:
def rmse(x, real_data):
    diff_sq = (x- real_data)**2
    return np.sqrt(diff_sq.mean())

a = np.array([1,2,3])
b = np.array([1,2,3])
rmse(a,b)


0.0

In [67]:
from spn.algorithms.Marginalization import marginalize
from copy import deepcopy


def next_error(model, data, num_time_steps=num_time_steps, num_dims=n_dim):
    unrolled_model = model.get_unrolled_rspn(model.get_len_sequence())
    for t in range(8, num_time_steps*n_dim+1, 4):

        prev_inputs = list(range(3, t-4, 4))
        spn_marg = marginalize(unrolled_model, list(range(t)))
        spn_marg = marginalize(spn_marg, prev_inputs)

        #remove inputs from previouss time steps
        inputs_to_include = []
        for i in range(t):
            if i not in prev_inputs:
                inputs_to_include.append(i)

        
        data_t = deepcopy(data)
        # print(f"==>> data.shape: {data.shape}")
        # print(f"==>> data_t.shape: {data_t.shape}")
        data_t[:, [t-2, t-3, t-4]] = [np.nan, np.nan, np.nan]
        print(f"==>> data_t: {data_t}")
        data_t = data_t[:, inputs_to_include]
        print(f"==>> data_t: {data_t}")
        break


In [68]:
test_ds0 = test_ds_list[0]

In [69]:
next_error(rspn_mimic_models[0], test_ds0[:2])

==>> child: In_LatentNode_1
==>> child: In_LatentNode_2
==>> child: In_LatentNode_139
==>> child: In_LatentNode_140
==>> child: In_LatentNode_141
==>> child: In_LatentNode_142
==>> child: In_LatentNode_143
==>> child: In_LatentNode_144
==>> child: In_LatentNode_145
==>> child: In_LatentNode_146
==>> data_t: [[ 67.  58.  16.   0.  nan  nan  nan   0.  67.  50.  12.   0.  72.  56.
   16.   0.  70.  65.  27.   0.  68.  52.  15.   0.  68.  52.  15.   0.
   79.  56.  23.   0.]
 [ 98.  83.  17.   0.  nan  nan  nan   0.  85.  71.  15.   0.  89.  80.
   13.   0.  93.  87.  12.   0. 103.  75.  19.   0.  97.  73.  19.   0.
   97.  80.  13.   0.]]
==>> data_t: [[67. 58. 16. nan nan nan  0.]
 [98. 83. 17. nan nan nan  0.]]
